In [8]:
import pandas as pd
from huggingface_hub import login
from datasets import load_dataset
import os
import json
import shutil

In [9]:
login(os.environ.get("HUG_TOKKEN"))

In [10]:
df_train = pd.read_csv('../fiszki-ocr/train/in.tsv', sep='\t', header=None, index_col=False)
files = [file[0] for file in df_train.iloc()]
df_train_out = pd.read_csv('../fiszki-ocr/train/expected.tsv', sep='\t', header=None, index_col=False)
files_out = [file_out[0] for file_out in df_train_out.iloc()]

In [18]:
whole = []
for file, out in zip(files, files_out):
        whole.append({"file_name": file, "ground_truth": json.dumps({"gt_parse": {"text_sequance": out}}, ensure_ascii=False)})

In [19]:
train = whole[:85]
validation = whole[85:]

In [20]:
train_files = [file.get("file_name") for file in train]
validation_files = [file.get("file_name") for file in validation]

In [14]:
for image in os.listdir("../fiszki-ocr/images"):
    if image in train_files:
        shutil.copy(f"/home/pc/work/fiszki-ocr/images/{image}", f"./images-split-fiszki/train/{image}")
    if image in validation_files:
        shutil.copy(f"/home/pc/work/fiszki-ocr/images/{image}", f"./images-split-fiszki/validation/{image}")

In [21]:

with open('./images-split-fiszki/train/metadata.jsonl', 'w', encoding='utf-8') as f:
    for entry in train:
        json.dump(entry, f, ensure_ascii=False)
        f.write("\n")
with open('./images-split-fiszki/validation/metadata.jsonl', 'w', encoding='utf-8') as f:
    for entry in validation:
        json.dump(entry, f, ensure_ascii=False)
        f.write("\n")
    

In [22]:
dataset = load_dataset('./images-split-fiszki')

Resolving data files:   0%|          | 0/86 [00:00<?, ?it/s]

Using custom data configuration images-split-fiszki-0b6e02834f7867a1


Extracting data files: 0it [00:00, ?it/s]

Extracting data files: 0it [00:00, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating validation split: 0 examples [00:00, ? examples/s]

Dataset imagefolder downloaded and prepared to /home/pc/.cache/huggingface/datasets/imagefolder/images-split-fiszki-0b6e02834f7867a1/0.0.0/37fbb85cc714a338bea574ac6c7d0b5be5aff46c1862c1989b20e0771199e93f. Subsequent calls will reuse this data.


  0%|          | 0/2 [00:00<?, ?it/s]

In [23]:
dataset.push_to_hub("Zombely/fiszki-ocr-train")

Pushing split train to the Hub.


  0%|          | 0/1 [00:00<?, ?ba/s]

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]

Pushing split validation to the Hub.


  0%|          | 0/1 [00:00<?, ?ba/s]

Pushing dataset shards to the dataset hub:   0%|          | 0/1 [00:00<?, ?it/s]